In [1]:
import pandas as pd
import numpy as np
import uuid
from datetime import datetime, timedelta
import random

In [2]:
%pip install numpy == 2.0

Note: you may need to restart the kernel to use updated packages.


ERROR: Invalid requirement: '=='

[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


#### Carga de datos

In [11]:
import os

print(os.getcwd())

C:\Users\carlo\Documents\dm_prueba_t-cnica\notebooks


In [12]:
os.chdir('C:/Users/carlo/Documents/dm_prueba_t-cnica/')

In [13]:
# cargar datos
print("Cargando datos...")
df = pd.read_csv('data/raw_sales_data.csv', sep=';')
df.shape

Cargando datos...


(50000, 9)

In [14]:
df.head()

order_id  customer_id  product_id  quantity  \
0  249093af-4bed-430f-a55d-73e8dd782870       7271.0       923.0      10.0   
1  8da511f7-ef36-4a18-9b31-1b107876ce28        861.0       621.0      20.0   
2  db3b8b9c-4917-4ec5-a7df-1c661aa6b69c       5391.0       677.0       3.0   
3  4aeec22a-d9bb-429c-9581-46068d89578a       5192.0       370.0       9.0   
4  1224d200-8fe1-4c9f-9ad2-546613fe1cc2          NaN         NaN      15.0   

        price  order_date region  discount shipping_priority  
0  410.048837  2024-06-07   East  0.064040               Low  
1  466.519110  2023-01-29   East  0.021410            Medium  
2   35.175263  2023-09-24   West  0.243724            Medium  
3   75.551426  2023-08-11   West  0.272166               Low  
4   61.812616  2024-08-09    NaN  0.233102              High

#### Realizo una revisión completa del dataset usando una librería de preferencia personal, en este caso Profiling

In [15]:
from ydata_profiling import ProfileReport

profile = ProfileReport(df, title='Reporte de Calidad de Datos', explorative=True)

In [16]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

#### En el reporte se logran evidenciar los valores faltantes, las atipicidades y alta correlación entre price y discount, por lo que se procede a la limpieza de datos.

In [17]:
#revisión manual

print("\nValores faltantes antes de limpieza:")
print(df.isna().sum())

# % nulos
missing_percentage = (df.isna().sum() / len(df)) * 100

print("\nPorcentaje de valores faltantes por columna:")
print(missing_percentage)


Valores faltantes antes de limpieza:
order_id               0
customer_id          609
product_id           617
quantity             623
price                666
order_date           931
region               614
discount             620
shipping_priority    636
dtype: int64

Porcentaje de valores faltantes por columna:
order_id             0.000
customer_id          1.218
product_id           1.234
quantity             1.246
price                1.332
order_date           1.862
region               1.228
discount             1.240
shipping_priority    1.272
dtype: float64


In [18]:
def clean_sales_data(df):
    """
    Limpia los datos de ventas aplicando las siguientes transformaciones:
    - Reemplaza valores extremos con NA
    - Elimina filas con valores faltantes en campos críticos
    - Imputa valores faltantes según reglas de negocio
    
    Args:
        df: DataFrame original
    Returns:
        DataFrame limpio
    """
    # copia para no modificar el original
    df2 = df.copy()
    
    # reemplazo valores extremos con NA
    df2 = df2.replace([-9999, -9999.99], np.nan)
    
    # eliminacion filas con campos críticos faltantes
    critical_columns = ['price', 'quantity', 'order_date']
    df2 = df2.dropna(subset=critical_columns)
    
    # imputacion IDs con el valor más frecuente
    for col in ['customer_id', 'product_id']:
        if df2[col].isna().any():
            df2[col] = df2[col].fillna(df2[col].mode()[0])
    
    # imputacion de descuentos basados en rangos de precio
    if df2['discount'].isna().any():
        price_ranges = pd.qcut(df2['price'], q=5)
        df2['discount'] = df2.groupby(price_ranges)['discount'].transform(
            lambda x: x.fillna(x.median())
        )
    
    # limpieza a  region y shipping_priority
    for col in ['region', 'shipping_priority']:
        df2[col] = df2[col].replace('UNKNOWN', np.nan)
        df2[col] = df2[col].fillna(df2[col].mode()[0])
    
    return df2

In [19]:
df2 = clean_sales_data(df)

C:\Users\carlo\AppData\Local\Temp\ipykernel_9968\28787029.py:31: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df2['discount'] = df2.groupby(price_ranges)['discount'].transform(


In [21]:
def generate_sales_report(df):
    """
    Genera un reporte de ventas con métricas clave.
    
    Args:
        df: DataFrame limpio con datos de ventas
    """
    # calcula ingreso neto si no existe
    if 'ingreso_neto' not in df.columns:
        df['ingreso_neto'] = df['price'] * df['quantity'] * (1 - df['discount'])
    
    # recoge todas las métricas
    reporte = {}
    
    # 1. Top 5 clientes
    ingresos_por_cliente = df.groupby('customer_id')['ingreso_neto'].sum().sort_values(ascending=False)
    reporte['top_clientes'] = ingresos_por_cliente.head()
    
    # 2. Productos por región
    productos_por_region = df.groupby(['region', 'product_id'])['quantity'].sum()
    reporte['productos_region'] = {}
    
    for region in df['region'].unique():
        top_producto = productos_por_region[region].idxmax()
        cantidad = productos_por_region[region].max()
        reporte['productos_region'][region] = {
            'producto': top_producto,
            'cantidad': cantidad
        }
    
    # 3. Ingresos por región
    reporte['ingresos_region'] = df.groupby('region')['ingreso_neto'].sum().sort_values(ascending=False)
    
    # Imprimir reporte formateado
    print("\n=== REPORTE DE VENTAS ===")
    print("\n1. TOP 5 CLIENTES POR INGRESO")
    print("-" * 30)
    for cliente, ingreso in reporte['top_clientes'].items():
        print(f"Cliente {cliente}: ${ingreso:,.2f}")
    
    print("\n2. PRODUCTO MÁS VENDIDO POR REGIÓN")
    print("-" * 30)
    for region, datos in reporte['productos_region'].items():
        print(f"Región {region}:")
        print(f"  Producto: {datos['producto']}")
        print(f"  Cantidad: {datos['cantidad']:,}")
    
    print("\n3. INGRESOS POR REGIÓN")
    print("-" * 30)
    for region, ingreso in reporte['ingresos_region'].items():
        print(f"Región {region}: ${ingreso:,.2f}")
    
    
    return reporte

In [22]:
# Ejemplo de uso:
reporte = generate_sales_report(df2)


=== REPORTE DE VENTAS ===

1. TOP 5 CLIENTES POR INGRESO
------------------------------
Cliente 2416.0: $677,852.65
Cliente 5701.0: $44,187.92
Cliente 8829.0: $43,940.16
Cliente 3412.0: $42,467.54
Cliente 2935.0: $41,110.43

2. PRODUCTO MÁS VENDIDO POR REGIÓN
------------------------------
Región East:
  Producto: 941.0
  Cantidad: 1,885.0
Región West:
  Producto: 941.0
  Cantidad: 565.0
Región North:
  Producto: 941.0
  Cantidad: 519.0
Región South:
  Producto: 941.0
  Cantidad: 446.0

3. INGRESOS POR REGIÓN
------------------------------
Región East: $29,055,248.55
Región North: $28,025,863.11
Región South: $27,959,507.72
Región West: $27,850,044.72


Se observa que el más vendido es el producto con el ID 941, entonces las regiones lo fue y la región de mayor ingreso fue la Oriental

In [ ]:
#Cálculo de la distribución de la prioridad en las regiones
print("\nDistribución de prioridad de envío por región:")
print(pd.crosstab(df2['region'], df2['shipping_priority'], normalize='index') * 100)


Distribución de prioridad de envío por región:
shipping_priority       High        Low     Medium
region                                            
East               29.995913  29.178586  40.825501
North              50.401741  19.919652  29.678607
South              19.638807  29.374213  50.986980
West               25.242473  29.754575  45.002952


En este caso la prioridad media tiene la mayor participación en la mayoría de regiones, exceptuando la región norte.

In [24]:
print("\nEstadísticas finales:")
print(f"Registros originales: {len(df)}")
print(f"Registros después de limpieza: {len(df2)}")
print("\nValores faltantes después de limpieza:")
print(df.isna().sum())

# algunas stats adicionales
print("\nResumen de fechas después de limpieza:")
print(df2['order_date'].describe())
print("\nResumen de precios después de limpieza:")
print(df2['price'].describe())
print("\nResumen de descuentos después de limpieza:")
print(df2['discount'].describe())


Estadísticas finales:
Registros originales: 50000
Registros después de limpieza: 47945

Valores faltantes después de limpieza:
order_id               0
customer_id          609
product_id           617
quantity             623
price                666
order_date           931
region               614
discount             620
shipping_priority    636
dtype: int64

Resumen de fechas después de limpieza:
count          47945
unique           730
top       2024-12-27
freq             145
Name: order_date, dtype: object

Resumen de precios después de limpieza:
count    47945.000000
mean       249.978208
std        144.216651
min          1.030168
25%        124.912708
50%        249.055797
75%        374.661866
max        499.992113
Name: price, dtype: float64

Resumen de descuentos después de limpieza:
count    47945.000000
mean         0.149274
std          0.087363
min          0.000000
25%          0.074323
50%          0.148408
75%          0.221960
max          0.300000
Name: discoun

Vuelvo a realizar el reporte con el dataset limpio

In [26]:
profile2 = ProfileReport(df2, title='Reporte de Calidad de Datos Cleaned', explorative=True)
profile2.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Se puede evidenciar que el dataset quedó limpio.

### Guardo el dataset limpio

In [27]:
df2.to_csv('data/cleaned_sales_data.csv',sep=";", index=False)